##############################################

**_GroupID - ShRaRa_**

**_Member:_**

**_Rajat Singh (2003130)_**

**_Raj Hans Khoiwal (2003129)_**

**_Shivam Sinoliya (2003132)_**

##############################################

**1. Implement the following operations (forward and backward pass)**

    (a) Matrix multiplication layer W X
    (b) Bias addition layer
    (c) Mean squared loss layer
    (d) Soft max layer
    (e) Sigmoid layer
    (f) Cross entropy loss layer

In [1]:
import math

# utility function for matrix multiplication layer
def matrixMultiplicationLayer(X, W):
    # X is of size m×n and W is of size n×k
    # Declare and Initialize resultant matrix N = XW of size m×k with 0's
    m = len(X)
    n = len(X[0])
    k = len(W[0])
    N = [[0 for _ in range(k)] for _ in range(m)]

    for a in range(m):
        for b in range(k):
            for c in range(n):
                N[a][b] += X[a][c] * W[c][b]
    
    # return the resultant N = XW
    return N


# utility function for bias addition layer
def biasAdditionLayer(N, B):
    # N is of size m×k and B is of size m×k
    # Declare and Initialize resultant matrix P = N + B of size m×k with 0's
    m = len(N)
    k = len(N[0])
    P = [[0 for _ in range(k)] for _ in range(m)]
    
    for i in range(m):
        for j in range(k):
            P[i][j] += N[i][j] + B[i][j]

    # return the resultant P = N + B
    return P


# utility function for squared mean loss layer
def meanSquaredLossLayer(P, Y):
    # P is of size m×k and Y is of size m×k
    # Declare and Initialize resultant loss L = Σ(P[i][j] - Y[i][j])^2
    m = len(P)
    k = len(P[0])
    L = 0
    
    for i in range(m):
        for j in range(k):
            L += (P[i][j] - Y[i][j])**2

    # return the resultant loss L = Σ(P[i][j] - Y[i][j])^2
    return L


# utility function for soft max layer
def softMaxLayer(P):
    # P is of size m×k
    # Declare and Initialize resultant matrix Q = softmax(P[i][j]) = (e^-P[i][j])/Σj(e^-P[i][j]) of size m×k with 0's
    m = len(P)
    k = len(P[0])
    Q = [[(math.exp(-P[i][j])) for j in range(k)] for i in range(m)]
    
    for i in range(m):
        sum = 0
        for j in range(k):
            sum += Q[i][j]
        for j in range(k):
            Q[i][j] /= sum

    # return the resultant Q = softmax(Pi) = (e^-P[i][j])/Σj(e^-P[i][j])
    return Q


# utility function for sigmoid layer
def sigmoidLayer(P):
    # P is of size m×1
    # Declare and Initialize resultant matrix Q = sigma(P) = 1 / (1 + e^-P) of size m×1 with 0's
    m = len(P)
    Q = [0 for _ in range(m)]

    # sigma(z) = 1 / (1 + e^-z)
    for i in range(m):
        Q[i] = 1/(1 + (math.exp(-P[i])))

    # return the resultant Q = sigma(P) = 1 / (1 + e^-P)
    return Q


# utility function for cross entropy loss layer
def crossEntropyLossLayer(Q, Y):
    # Q is of size m×1 and Y is of size m×1
    # Declare and Initialize resultant loss L = -ΣΣ(Y[i][j]*log(Q[i][j])
    m = len(Q)
    k = len(Q[0])
    L = 0

    for i in range(m):
        for j in range(k):
            L += -(Y[i][j]*math.log(Q[i][j]))

    # return the cross entropy loss L = -ΣΣ(Y[i][j]*log(Q[i][j])
    return L

**2. Using the sklearn.load boston() function, obtain boston house pricing dataset.
Train a regression model using the operations implemented above. You need to
write a stochastic gradient descent function to train.**

In [2]:
#importing boston house pricing data-set from URL since it's formally removed from sklearn
import pandas as pd
import numpy as np

data_url = "http://lib.stat.cmu.edu/datasets/boston"
raw_df = pd.read_csv(data_url, sep="\s+", skiprows=22, header=None)
data_boston = np.hstack([raw_df.values[::2, :], raw_df.values[1::2, :2]])
result_boston = raw_df.values[1::2, 2]
# print("data_boston", data_boston)
# print("result_boston", result_boston)
print(data_boston.shape)
print(result_boston.shape)


(506, 13)
(506,)


**_Used to generate W, B, Batches of X and Y of given size_**

In [3]:
import random

# utility function for generating Feature weights matrix W
def generateFeatureWeightsW(number_of_features, number_of_neuron_layers):
    W = [[random.random() for _ in range(number_of_neuron_layers)]
         for _ in range(number_of_features)]
    return W


# utility function for generating Bias-matrix B
def generateBias(batch_size, number_of_neuron_layers):
    x = random.random()
    B = [[x for _ in range(number_of_neuron_layers)] for _ in range(batch_size)]
    return B


# utility function for generate a batch of X and Y from the data and result
def generateBatch(batch_size, batch_number, data, result):
    X = data[batch_number : (batch_number+batch_size)]
    Y = result[batch_number : (batch_number+batch_size)]
    return X, Y


# utility function to convert 1-D list to 2-D matrix
def reshape(M):
    m = len(M)
    Y = [[0 for _ in range(1)] for _ in range(m)]

    for i in range(m):
        Y[i][0] = M[i]

    return Y

In [4]:
# utility function to find the gradient of loss w.r.t. P
def gradientLossWrtP(P, Y):
    m = len(P)
    k = len(P[0])
    d_LP = [[2*(P[i][j] - Y[i][j]) for j in range(k)] for i in range(m)]
    return d_LP


# utility function to find the gradient of loss w.r.t. B
def gradientLossWrtB(d_LP):
    d_LB = 0

    for i in range(len(d_LP)):
        for j in range(len(d_LP[0])):
            d_LB += d_LP[i][j]
            
    return d_LB


# utility function to bias B using gradient descent
def trainB(B, d_LB, alpha):
    m = len(B)
    k = len(B[0])
    new_B = [[(B[i][j] - alpha*d_LB) for j in range(k)] for i in range(m)]
    return new_B


# utility function to find the transpose of the matrix
def tranpose(X):
    m = len(X)
    n = len(X[0])
    X_transpose = [[0 for _ in range(m)] for _ in range(n)]

    for i in range(n):
        for j in range(m):
            X_transpose[i][j] = X[j][i]

    # return the resultant X = X'
    return X_transpose


# utility function to find the gradient of loss w.r.t. W
def gradientLossWrtW(X, d_LP):
    X_transpose = tranpose(X)
    d_LN = d_LP
    d_LW = matrixMultiplicationLayer(X_transpose, d_LN)
    return d_LW


# utility function to feature weights W using gradient descent
def trainW(W, d_LW, alpha):
    m = len(W)
    k = len(W[0])
    new_W = [[(W[i][j] - alpha*d_LW[i][j]) for j in range(k)] for i in range(m)]
    return new_W

In [5]:
number_of_features = len(data_boston[0])  # number of featrues of a sample
number_of_neuron_layers = 1
batch_size = int(input("Enter the batch size: ")) # user input of batch size



# generate feature weights W and bias B
W = generateFeatureWeightsW(number_of_features, number_of_neuron_layers)
B = generateBias(batch_size, number_of_neuron_layers)


number_of_iterations = len(data_boston)//batch_size

for _ in range(1000):
    batch_number = 0 # initialize batch number to 0 i.e. start index of first batch sample
    for i in range(number_of_iterations):
        # forward-pass
        X, Y = generateBatch(batch_size, batch_number,
                             data_boston, result_boston)
        Y = reshape(Y)                              # converting Y to matrix form
        N = matrixMultiplicationLayer(X, W)         # N = XW
        P = biasAdditionLayer(N, B)                 # P = N + B
        L = meanSquaredLossLayer(P, Y)              # L = Σ(P[i] - Y[i])^2

        # backward-pass
        alpha = pow(10, -10)                # since the data is non-linear, we need to slow the learning rate else it will shoot to [nan]
        d_LP = gradientLossWrtP(P, Y)       # dL/dP
        d_LB = gradientLossWrtB(d_LP)       # dL/dB
        B = trainB(B, d_LB, alpha)          # train B
        d_LW = gradientLossWrtW(X, d_LP)    # dl/dW
        W = trainW(W, d_LW, alpha)          # train W

        # print result
        print(f"iter-{i+1}:")
        print(f"loss = {L}")
        # print(f"W:\n{W}")
        # print(f"B:\n{B}")
        # increment batch_number
        batch_number += batch_size

iter-1:
loss = 312765.7670686405
iter-2:
loss = 389094.2119852398
iter-3:
loss = 395928.36789167236
iter-4:
loss = 342489.5927673999
iter-5:
loss = 402842.44132785435
iter-6:
loss = 335847.5180044532
iter-7:
loss = 310473.77694835496
iter-8:
loss = 370787.6806967308
iter-9:
loss = 338078.7716679766
iter-10:
loss = 362580.2913683262
iter-11:
loss = 436257.10673524777
iter-12:
loss = 485722.03544458625
iter-13:
loss = 404974.76389229053
iter-14:
loss = 470499.7946647391
iter-15:
loss = 346232.690764438
iter-16:
loss = 393804.52960651286
iter-17:
loss = 377891.63619438343
iter-18:
loss = 320501.7847145957
iter-19:
loss = 386657.05312747776
iter-20:
loss = 288866.2510420277
iter-21:
loss = 324625.5273201355
iter-22:
loss = 407825.29601456644
iter-23:
loss = 414651.2700240895
iter-24:
loss = 385950.14626109076
iter-25:
loss = 360787.47722485935
iter-26:
loss = 433304.8520801243
iter-27:
loss = 423199.6217407768
iter-28:
loss = 474077.1787337292
iter-29:
loss = 496838.7846836414
iter-30:
los

**3. Load the iris dataset in sklearn. This data sets consists of 3 different types of irises’ (Setosa, Versicolour, and Virginica) petal and sepal length, stored in a 150x4 numpy.ndarray. Using the operations implemented above create a multi- class classifier (Cross entropy loss + soft max)**

In [6]:
# importing iris dataset from sklearn
from sklearn.datasets import load_iris
iris = load_iris()

# Store features matrix in data
data_iris = iris.data
# Store target vector in result
result_iris = iris.target

# Names of features/columns in iris dataset
print(iris.feature_names)
# print(data)
# print(result)
print(data_iris.shape)
print(result_iris.shape)


['sepal length (cm)', 'sepal width (cm)', 'petal length (cm)', 'petal width (cm)']
(150, 4)
(150,)


In [7]:
# utility function to reshape the Y to m×k matrix such that each row is {0,1} where 0 if Y!=Y else 1
def classifier_reshape(X, number_of_neuron_layers):
    m = len(X)
    Y = [[0 for _ in range(number_of_neuron_layers)] for _ in range(m)]

    for i in range(m):
        Y[i][X[i]] = 1

    return Y


# utility function to find the gradient of loss w.r.t. P for cross-entrop[y loss
def gradientLossWrtP_CEL(Y, Q):
    m = len(Y)
    k = len(Y[0])
    # refer to the derivation pasted in the image just below
    d_LP = [[Y[i][j]*(1 - Q[i][j]) for j in range(k)] for i in range(m)]

    return d_LP

![image info](https://raw.githubusercontent.com/RajatSingh08/RajatSingh08/main/Screenshot%20from%202023-01-24%2017-41-31.png)

In [8]:
number_of_features = len(data_iris[0])  # number of featrues of a sample
# number of neuron layers = number of values Y can take
number_of_neuron_layers = len(set(result_iris))
# print(number_of_neuron_layers)

batch_size = int(input("Enter the batch size: "))  # user input of batch size



# generate feature weights W and bias B
W = generateFeatureWeightsW(number_of_features, number_of_neuron_layers)
B = generateBias(batch_size, number_of_neuron_layers)


number_of_iterations = len(data_iris)//batch_size

for _ in range(1000):
    batch_number = 0  # initialize batch number to 0 i.e. start index of first batch sample
    for i in range(number_of_iterations):
        # forward-pass
        X, Y = generateBatch(batch_size, batch_number, data_iris, result_iris)
        Y = classifier_reshape(Y, number_of_neuron_layers)                   # converting Y to matrix form
        N = matrixMultiplicationLayer(X, W)         # N = XW
        P = biasAdditionLayer(N, B)                 # P = N + B
        Q = softMaxLayer(P)                         # Q = softmax(P)
        L = crossEntropyLossLayer(Q, Y)             # L = ΣΣY[i][j]log(Q[i][j])

        # backward-pass
        # since the data is non-linear, we need to slow the learning rate else it will shoot to [nan]
        alpha = pow(10, -5)
        d_LP = gradientLossWrtP_CEL(Y, Q)       # dL/dPij = Yij(1-Qij) ...... refer the derivation above
        d_LB = gradientLossWrtB(d_LP)       # dL/dB
        B = trainB(B, d_LB, alpha)          # train B
        d_LW = gradientLossWrtW(X, d_LP)    # dl/dW
        W = trainW(W, d_LW, alpha)          # train W

        # print result
        print(f"iter-{i+1}:")
        print(f"loss = {L}")
        # print(f"W:\n{W}")
        # print(f"B:\n{B}")
        # increment batch_number
        batch_number += batch_size


iter-1:
loss = 0.19514133563285843
iter-2:
loss = 0.19520927865320803
iter-3:
loss = 0.18442921441340124
iter-4:
loss = 0.10966849393003048
iter-5:
loss = 0.16176477873576095
iter-6:
loss = 0.1806249948771319
iter-7:
loss = 0.1546022666277369
iter-8:
loss = 0.18203035588245764
iter-9:
loss = 0.2012128058544963
iter-10:
loss = 0.17728437769506014
iter-11:
loss = 21.14979891721481
iter-12:
loss = 19.47356943040743
iter-13:
loss = 18.739623897940447
iter-14:
loss = 19.448287590588023
iter-15:
loss = 20.302845014013727
iter-16:
loss = 20.67155693277454
iter-17:
loss = 18.65750723212647
iter-18:
loss = 20.11081325166534
iter-19:
loss = 18.443576692706024
iter-20:
loss = 19.131481023078862
iter-21:
loss = 20.696968483330895
iter-22:
loss = 21.48897263407658
iter-23:
loss = 20.829925173801804
iter-24:
loss = 22.030710682884546
iter-25:
loss = 21.81246833622246
iter-26:
loss = 22.087674558073665
iter-27:
loss = 22.085265767669505
iter-28:
loss = 22.45074880711187
iter-29:
loss = 22.01063786087